## Connect to API

In [1]:
# this code allows us to run the internal packages

import os
import sys

parent_directory = os.path.split(os.getcwd())[0]

import_path = parent_directory + '/data_models'

if import_path not in sys.path:
    sys.path.insert(0, import_path)

In [2]:
from api import Api
from datetime import datetime

from cmr.get_metadata import *

In [3]:
production = Api('production')

In [4]:
test = Api('test')

In [5]:
def convert_date(date_string):
    date_list = [int(x) for x in date_string.split('-')]
    return datetime(*date_list)

## Query Database

In [6]:
def build_dict(server):
    camp_data = {}
    
    # get the campaigns
    campaigns = server.get('campaign')
    camp_data = {camp['uuid']:{'short_name':camp['short_name'], 'uuid':camp['uuid'], 'deployments':[]} for camp in campaigns['data']}
    print(camp_data[list(camp_data.keys())[0]])

    # get the deployments 
    deployments = server.get('deployment')
    dep_data = {dep['uuid']:{'uuid':dep['uuid'], 'start_date':dep['start_date'], 'end_date':dep['end_date'], 'campaign': dep['campaign'], 'flights':[]} for dep in deployments['data']}
    print(dep_data[list(dep_data.keys())[0]])

    # get the flights
    flights = server.get('collection_period')
    flight_data = flights['data']

    # build the mega dictionary
    for flight in flights['data']:
        dep_data[flight['deployment']]['flights'].append(flight)
    for deployment_uuid, deployment_data in dep_data.items():
        camp_data[deployment_data['campaign']]['deployments'].append(deployment_data)

    # add CMR to the data tree
    # loop through all campaigns in database
    for campaign_uuid, campaign in camp_data.items():
        # skip DC3, since it fails
        if campaign['short_name']=='DC3':
            continue
        print(campaign['short_name'])
        for deployment in campaign['deployments']:
            start = convert_date(deployment['start_date'])
            end = convert_date(deployment['end_date'])
            print('    ', start, '-', end)
            cmr_data = get_deployment_and_cp(campaign['short_name'], start, end)
            deployment['cmr'] = cmr_data
            
    return camp_data

In [7]:
prod_data = build_dict(production)

{'short_name': 'ACES', 'uuid': '951482fa-5748-46ba-aed5-aab8b106b103', 'deployments': []}
{'uuid': '3a09cded-e13e-41fc-915c-0b9aec4bcbc1', 'start_date': '2012-08-28', 'end_date': '2012-11-06', 'campaign': 'c1e56561-6726-4832-8dbe-0453b10ff36c', 'flights': []}
ACES
     2002-08-02 00:00:00 - 2002-08-30 00:00:00
         C1694294472-GHRC_CLOUD success
         C1625128595-GHRC_CLOUD success
         C1625128914-GHRC_CLOUD success
         C1625128385-GHRC_CLOUD success
         C1625128567-GHRC_CLOUD success
         C1625128568-GHRC_CLOUD success
{'concept_id': 'C1694294472-GHRC_CLOUD', 'metadata': {'CollectionCitations': [{'OtherCitationDetails': 'Blakeslee, Richard J., Douglas M. Mach and Richard  Wolhman.2004. ACES Aircraft and Mechanical Data [indicate subset used]. Dataset available online from the NASA Global Hydrology Resource Center DAAC, Huntsville, Alabama, U.S.A. DOI: http://dx.doi.org/10.5067/ACES/MULTIPLE/DATA101'}], 'SpatialExtent': {'SpatialCoverageType': 'HORIZONTAL', 'H

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [56]:
test_data = build_dict(test)

{'short_name': 'CARVE', 'uuid': '3d42927c-4a55-4bea-9e6f-1d53d870965c', 'deployments': []}
{'uuid': 'a315c8a5-a1ef-40b1-8e34-9702cfe6b08b', 'start_date': '2012-08-28', 'end_date': '2012-11-06', 'campaign': 'ec77afcb-d280-4d77-a4c1-4bb79a5a76d7', 'flights': []}
CARVE
     2012-05-23 00:00:00 - 2012-10-30 00:00:00
         C1400101586-ORNL_DAAC success
         C1299758974-ORNL_DAAC success
         C1000000661-ORNL_DAAC success
         C1000000520-ORNL_DAAC success
         C1248454738-ORNL_DAAC success
         C1420459165-ORNL_DAAC success
         C1420654406-ORNL_DAAC success
         C1511758943-ORNL_DAAC success
         C1329921126-ORNL_DAAC success
         C1420654430-ORNL_DAAC success
         C1420654607-ORNL_DAAC success
         C1373782713-ORNL_DAAC success
         C1372809456-ORNL_DAAC success
         C1372808917-ORNL_DAAC success
         C1358003823-ORNL_DAAC success
         C1373450312-ORNL_DAAC success
         C1292501250-ORNL_DAAC success
         C1292500395-OR

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



## Explore Data

In [57]:
len(prod_data)

10

In [58]:
len(test_data)

11

In [10]:
prod_aces = prod_data['951482fa-5748-46ba-aed5-aab8b106b103']

In [11]:
[(key, item['short_name']) for key, item in test_data.items()]

[('3d42927c-4a55-4bea-9e6f-1d53d870965c', 'CARVE'),
 ('235ecec0-7314-4ecc-990d-b909b498b636', 'ACES'),
 ('928c0f13-543e-4647-84bf-6c5620c77055', 'DC3'),
 ('74310c1a-cfc3-44f4-bf47-5e591f570f24', 'GCPEx'),
 ('6912a5fc-e7ee-4d8a-9826-c67ee6a7e100', 'GOES-R PLT'),
 ('b50f89d5-e728-474f-84cc-809a9851fd27', 'GRIP'),
 ('ec77afcb-d280-4d77-a4c1-4bb79a5a76d7', 'HS3'),
 ('441e3b68-62ba-4674-b8e2-5942c75e868d', 'OLYMPEX'),
 ('ca30e8ad-6631-42d2-8595-d4733b562657', 'ARCTAS'),
 ('48dd8b25-09a4-492d-9acd-3233afacdcbe', 'AirMOSS'),
 ('081535a6-8398-4fb7-a0a8-e918bee53c74', 'a_delete_me')]

In [62]:
test_aces = test_data['235ecec0-7314-4ecc-990d-b909b498b636']

In [59]:
print('number of ACES deployments', len(prod_aces['deployments']))
flights = prod_aces['deployments'][0]['flights']
print('number of aces flights', len(flights))

number of ACES deployments 1
number of aces flights 19


In [64]:
print('number of ACES deployments', len(test_aces['deployments']))
test_flights = test_aces['deployments'][0]['flights']
print('number of aces flights', len(flights))

number of ACES deployments 1
number of aces flights 19


In [65]:
print('flights with their current platforms and instruments')
platform_uuids = []
for flight in test_flights:
    platform_uuids.append(flight['platform'])
    print(test.gmcd_shorts('platform', flight['platform']))
    print('    ', [test.gmcd_shorts('instrument', uuid) for uuid in flight['instruments']])

flights with their current platforms and instruments
['ALTUS']
     [[''], ['DOPS'], [], ['ELECTRIC FIELD MILL'], ['FGM'], ['GERDIEN CONDUCTIVITY PROBE'], [], []]
['BALLOONS']
     [[], []]
['ROCKETS']
     [['ROCKETSONDES']]
[]
     [['RASS']]
[]
     [[], [], [], [], [], [], []]


In [61]:
print('flights with their current platforms and instruments')
platform_uuids = []
for flight in test_flights:
    platform_uuids.append(flight['platform'])
    print(test.gmcd_shorts('platform', flight['platform']))
    print('    ', [test.gmcd_shorts('instrument', uuid) for uuid in flight['instruments']])

flights with their current platforms and instruments
['ALTUS']
     [['ELECTRIC FIELD MILL'], []]
['ALTUS']
     [[]]
['ALTUS']
     [['GERDIEN CONDUCTIVITY PROBE']]
['ALTUS']
     [[]]
['ALTUS']
     [['DOPS']]
['ALTUS']
     [['FGM']]
['ALTUS']
     [['']]
['ALTUS']
     [[]]
['BALLOONS']
     [[], []]
['BALLOONS']
     [[]]
['ROCKETS']
     [['ROCKETSONDES']]
[]
     [['RASS']]
[]
     [[], []]
[]
     [[]]
[]
     [[]]
[]
     [[]]
[]
     [[]]
[]
     [[]]
[]
     [[]]


In [ ]:
# platform_updates = {platform_uuid: {instruments: [inst_uuids], flight_to_keep: flight_uuid}
delete_flights = []
platform_updates = {}

for flight in flights:
    if flight['platform'] in platform_updates.keys():
        delete_flights.append(flight['uuid'])
        platform_updates[flight['platform']]['instruments'].extend(flight['instruments'])
        platform_updates[flight['platform']]['instruments'] = list(set(platform_updates[flight['platform']]['instruments']))
    else:
        platform_updates[flight['platform']] = {
            'instruments':flight['instruments'],
            'flight_to_keep':flight['uuid']
        }

In [16]:
delete_flights = []
all_updates = {}

for campaign_uuid, campaign in test_data.items():
    for deployment in campaign['deployments']:
        platform_updates = {}
        for flight in deployment['flights']:
            if flight['platform'] in platform_updates.keys():
                delete_flights.append(flight['uuid'])
                platform_updates[flight['platform']]['instruments'].extend(flight['instruments'])
                platform_updates[flight['platform']]['instruments'] = list(set(platform_updates[flight['platform']]['instruments']))
            else:
                platform_updates[flight['platform']] = {
                    'instruments':flight['instruments'],
                    'flight_to_keep':flight['uuid']
                }
        all_updates[deployment['uuid']]=platform_updates

In [17]:
for dep_uuid, deployment in all_updates.items():
    print('dep uuid:', dep_uuid)
    for plat_uuid, platform in deployment.items():
        print(platform['instruments'])

dep uuid: f9a05746-d7b9-41ef-b4b7-405bfb925526
['45abac7a-f9a0-4feb-acae-421ee5cc7ade', 'ddcc1b52-7a74-494a-8c24-f1de6266501a', '1b0a4223-a2de-4ed3-af51-db967622b649', '4cb55b7e-90a1-40c9-93e7-8830aa88d91f', '3361a04a-25be-4c87-b754-bf136f5152b9', 'bc450383-dbf6-41b8-bd7a-85b7eef66bd6']
['1b0a4223-a2de-4ed3-af51-db967622b649', '3361a04a-25be-4c87-b754-bf136f5152b9']
dep uuid: 61a8abb0-aeed-475d-a02a-3bfb2afeabc3
['45abac7a-f9a0-4feb-acae-421ee5cc7ade', 'ddcc1b52-7a74-494a-8c24-f1de6266501a', '1b0a4223-a2de-4ed3-af51-db967622b649', '4cb55b7e-90a1-40c9-93e7-8830aa88d91f', '3361a04a-25be-4c87-b754-bf136f5152b9', 'bc450383-dbf6-41b8-bd7a-85b7eef66bd6']
['1b0a4223-a2de-4ed3-af51-db967622b649', '3361a04a-25be-4c87-b754-bf136f5152b9']
dep uuid: 31c68ab7-e7b0-464f-aca3-22ab0a129994
['45abac7a-f9a0-4feb-acae-421ee5cc7ade', 'ddcc1b52-7a74-494a-8c24-f1de6266501a', '1b0a4223-a2de-4ed3-af51-db967622b649', '4cb55b7e-90a1-40c9-93e7-8830aa88d91f', '3361a04a-25be-4c87-b754-bf136f5152b9', 'bc450383-dbf6

In [28]:
flights_to_keep = []
for dep_uuid, deployment in all_updates.items():
#     print('dep uuid:', dep_uuid)
    for plat_uuid, platform in deployment.items():
        print(platform['flight_to_keep'])
        flights_to_keep.append(platform['flight_to_keep'])

5a2156c5-8501-4ed8-a97b-6b0caea36677
e5a36597-072d-410c-ac92-629c24be0db9
4c5aa2f6-fef4-4c35-b040-7ae144ab001d
af69d37c-b101-4bb5-b651-012628bc81a4
5d8fc4b9-ed30-4f99-aedc-7e0d281977e5
fba2c2dd-6108-468d-93c6-5b86487e8162
def9aa27-8985-4825-905a-da8ede20d8a7
c231556a-b711-4bec-bf25-7304ec73f1c8
6874dafe-9f65-43cb-9b3a-2a637c90b2eb
7346306f-eae5-4a73-87cd-40eacdf0074d
7b3c65a5-94ab-44c1-803b-170d6c51d7cd
17d6cc3b-b4d6-4733-8d1c-a46c5517af80
7c021b39-e39c-419c-b120-03354a3bba64
0a9ad45c-bd99-42dd-968f-0dc28ecfc71c
ec916f63-baac-401c-8013-6f8a59c34336
b5a6493d-ce5e-4885-bfea-0c2c485e7e1b
3c3cc09b-092e-4d69-8cd5-1b0241ceafc0
328c55ce-1472-4179-8f0e-36bc71ea5b87
9c67a15c-e833-45be-88fc-e9e7e593f9d5
d53d373a-187a-4582-a5eb-5e47868e4974
0a8606e1-3e10-49c2-b436-2e88939edb79
c658eff9-c212-42f2-81bc-5dac2a3c7ebc
cc7a0759-41af-4bee-8bb4-6e0145bc73f3
e7c698f9-40bb-4c10-a318-f3d28917de6b
f3827c09-07e7-4986-b2bd-ac8a82cc1ed4
e1a1fb07-7232-4f65-88d0-e7e63f1e182f
5390d9e5-989d-4da8-a2b4-c767cab548c9
4

## Delete Flights

In [35]:
len(delete_flights)

312

In [36]:
delete_flights

['a50c7176-cd0a-4f45-8ae0-18503b164af4',
 'f76c0485-674e-4508-808e-fdb6b90550a6',
 'ee607138-2eff-47b2-b400-4b7fb81bb613',
 'cc3e3466-6116-48af-8114-8c7cd8b99006',
 '169016c7-1e1e-4d90-9eef-b5bcd098dd86',
 'c0ccac68-73d1-4251-960e-6f86e00934bd',
 '626d36ed-4642-467b-8eec-9bf1ad97bcf4',
 'a8916c30-512c-43d5-9a64-03de0ab87f9e',
 '718433cc-2040-4761-a3af-55d51ad0f89b',
 '6de8ed5e-8d42-48f2-8eff-f5686b09a85e',
 'f7e8216c-a8e6-419c-b40e-a109a0cd9922',
 '0212870b-a19e-49ae-8320-dacf6952c24b',
 '34e03922-e7d4-44ce-97a7-efb32cfef96d',
 '8774a788-8819-4437-9af2-6d2eb9f57d97',
 'f7742ee7-40ae-4114-bd80-c17e64e5e950',
 'b6005684-538a-4925-8526-1f2b01467622',
 '136a32c1-8124-468f-b642-aea577218936',
 '8ab3913a-dff9-49cc-a186-04dc11ba034d',
 'e4c4fb97-af1c-4f62-8d26-aa0cd0104135',
 '948ed271-ee1c-4acc-bc2f-17a355d4b49c',
 '7795818c-e370-433f-9a3a-c1a4a8925542',
 '3579c266-319c-4705-8f73-21ac9242fa83',
 '222fec85-f99d-448e-bd08-ca4c407c2d23',
 '0f32200b-7b83-4d14-862d-e5abcb80d410',
 'bc514d5e-a6ef-

In [40]:
for flight in delete_flights:
    test.delete(f'collection_period/{flight}')

In [39]:
test.get('collection_period/a50c7176-cd0a-4f45-8ae0-18503b164af4')['data']

{'uuid': 'a50c7176-cd0a-4f45-8ae0-18503b164af4',
 'asp_long_name': 'C-23 Sherpa -WFF',
 'platform_identifier': 'N430NA',
 'home_base': 'WFF',
 'campaign_deployment_base': 'Fairbanks International Airport',
 'platform_owner': 'NASA',
 'platform_technical_contact': 'Mike Cropper',
 'instrument_information_source': 'https://carve.ornl.gov/documentation.html , https://carve.ornl.gov/dataproducts.html , https://airbornescience.nasa.gov/aircraft/C-23_Sherpa_-_WFF',
 'notes_internal': '',
 'notes_public': '',
 'num_ventures': None,
 'auto_generated': True,
 'deployment': 'f9a05746-d7b9-41ef-b4b7-405bfb925526',
 'platform': 'e0f88864-3a65-4475-ae6d-ef86db5f2651',
 'dois': [],
 'instruments': ['ddcc1b52-7a74-494a-8c24-f1de6266501a']}

## Supplement Flights

In [29]:
len(set(flights_to_keep))

152

In [55]:
for dep_uuid, deployment in all_updates.items():
    
    for plat_uuid, flight_data in deployment.items():
        
        flight_uuid = flight_data['flight_to_keep']
        data = {'instruments':flight_data['instruments']}
        
        test.update(f'collection_period/{flight_uuid}', flight_data)